In [1]:
import sys
sys.path.append("../scripts/")
from robot import *
from scipy.stats import multivariate_normal

In [7]:
class Particle:
    def __init__(self, init_pose):
        self.pose = init_pose

    def motion_update(self, nu, omega, time, noise_rate_pdf):
        ns = noise_rate_pdf.rvs() # 順にnn, no, on, oo
        # 速度に雑音を加える
        noised_nu = nu + ns[0]*math.sqrt(abs(nu)/time) + ns[1]*math.sqrt(abs(omega)/time)
        # 角速度に雑音を加える
        noised_omega = omega + ns[2]*math.sqrt(abs(nu)/time) + ns[3]*math.sqrt(abs(omega)/time)
        # 姿勢を更新する
        self.pose = IdealRobot.state_transition(noised_nu, noised_omega, time, self.pose)

    def observation_update(self, observation):
        print('sensor: ', observation)

In [8]:
class Mcl:
    def __init__(self, init_pose, num, motion_noise_stds={"nn":0.19, "no":0.001, "on":0.13, "oo":0.2}):
        self.particles = [Particle(init_pose) for i in range(num)]

        v = motion_noise_stds # 標準偏差σabに対応

        # ４次元のガウス分布のオブジェクトを作る
        c = np.diag([v["nn"]**2, v["no"]**2, v["on"]**2, v["oo"]**2]) # 対角行列を作って返す
        self.motion_noise_rate_pdf = multivariate_normal(cov=c)

    def motion_update(self, nu, omega, time):
        for p in self.particles: p.motion_update(nu, omega, time, self.motion_noise_rate_pdf)
                                                             
    def draw(self, ax, elems):
        # 全パーティクルのX座標、Y座標をリスト化する
        xs = [p.pose[0] for p in self.particles]
        ys = [p.pose[1] for p in self.particles]

        # パーティクルの向きを描画するために、向きをベクトルで表したときのX座標、Y座標成分のリストを作る
        vxs = [math.cos(p.pose[2]) for p in self.particles]
        vys = [math.sin(p.pose[2]) for p in self.particles]
        
        elems.append(ax.quiver(xs, ys, vxs, vys, color="blue", alpha=0.5))

    def observation_update(self, observation):
        for p in self.particles: p.observation_update(observation)

In [9]:
class EstimationAgent(Agent):
    def __init__(self, time_interval, nu, omega, estimator):
        super().__init__(nu, omega)
        self.estimator = estimator
        self.time_interval = time_interval

        self.prev_nu = 0.0
        self.prev_omega = 0.0

    def decision(self, observation=None):
        # 一つ前の制御指令値でパーティクルの姿勢を更新する
        self.estimator.motion_update(self.prev_nu, self.prev_omega, self.time_interval)
        self.prev_nu, self.prev_omega = self.nu, self.omega
        self.estimator.observation_update(observation)
        return self.nu, self.omega
    
    def draw(self, ax, elems):
        self.estimator.draw(ax, elems)

In [ ]:
time_interval = 0.1
world = World(30, time_interval, debug=True)

# 地図を生成して3つランドマークを追加
m = Map()
for ln in [(-4, 2), (2, -3), (3, 3)]: m.append_landmark(Landmark(*ln))
world.append(m)

# ロボットを作る
initial_pose = np.array([0, 0, 0]).T # 初期位置を原点に
estimator = Mcl(initial_pose, 100)
a = EstimationAgent(time_interval, 0.2, 10.0/180*math.pi, estimator)
r = Robot(initial_pose, sensor=Camera(m), agent=a, color="red")
world.append(r)

world.draw()

sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -0.99746303]), 1), (array([3.24638594, 0.76111501]), 2)]
sensor:  [(array([ 2.48969566, -